## Load libraries

In [1]:
import numpy as np
import pandas as pd
import re
from scipy import stats
from scipy.stats import boxcox
from scipy.special import inv_boxcox
import math
import matplotlib.pyplot as plt
from sklearn.linear_model import LinearRegression, ElasticNet, Ridge, Lasso, BayesianRidge, LassoLarsIC
from sklearn.ensemble import RandomForestRegressor as rfr,  GradientBoostingRegressor
from sklearn.kernel_ridge import KernelRidge
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import RobustScaler
from sklearn.base import BaseEstimator, TransformerMixin, RegressorMixin, clone
from sklearn.model_selection import KFold, cross_val_score, train_test_split
from sklearn.metrics import mean_squared_error, SCORERS

import lightgbm as lgb
import xgboost as xgb
from catboost import CatBoostRegressor


%matplotlib inline
plt.style.use('ggplot')
from IPython.display import display
display.max_columns = None
display.max_rows = None

/Users/melaniezheng/opt/anaconda3/lib/python3.7/site-packages/lightgbm/__init__.py:48: UserWarning: Starting from version 2.2.1, the library file in distribution wheels for macOS is built by the Apple Clang (Xcode_8.3.3) compiler.
This means that in case of installing LightGBM from PyPI via the ``pip install lightgbm`` command, you don't need to install the gcc compiler anymore.
Instead of that, you need to install the OpenMP library, which is required for running LightGBM on the system with the Apple Clang compiler.
You can install the OpenMP library by the following command: ``brew install libomp``.
  "You can install the OpenMP library by the following command: ``brew install libomp``.", UserWarning)


## Load Data

In [2]:
train = pd.read_csv('../data/train_processed.csv')
test_raw = pd.read_csv('../data/test.csv')
train_raw=pd.read_csv('../data/train.csv')
test = pd.read_csv('../data/test_processed.csv')
yt = stats.boxcox(train['SalePrice'], lmbda = 0.3) # Boxcox of SalePrice
act_pred = train['SalePrice']
X = train.drop(columns='SalePrice')
X = X.loc[:, X.columns!='HouseStyle_2.5Fin'] #HouseStyle_2.5Fin in training.csv but not in test.csv

## Skewness (adjust Skewness of numeric columns)
 - Adjust features with skewness greater than 0.75

In [3]:
numeric=X.loc[:, X.columns != 'IsPool']
numeric = numeric.loc[:, numeric.columns !='IsGarage']
numerical = numeric.dtypes[:27].index.to_list()
skewed = X[numerical].apply(lambda x: x.skew()).sort_values()
skewdf = pd.DataFrame({'Skew': skewed})
skewdf = skewdf[(skewdf)>0.75]
from scipy.special import boxcox1p
skewed = skewdf.index
lam = 0.15
for feat in skewed:
    X[feat] = boxcox1p(X[feat], lam)
    test[feat] = boxcox1p(test[feat], lam)
# newskewed = X[numerical].apply(lambda x: x.skew()).sort_values()

## Evaluate Models

In [4]:
### This function returns Root Mean Squared Error for 5 fold cross validation tests.
### To compare side by side with Kaggle score.
def cv_rmse(model, X=X, yt=yt):
    y=train['SalePrice']
    kfold = KFold(n_splits=5, shuffle=True, random_state=1)
    RMSE_list=[]
    for train_id, holdout_id in kfold.split(X, yt):
        instance = clone(model)
        instance.fit(X.iloc[train_id], yt[train_id])
        y_pred = instance.predict(X.iloc[holdout_id])
        y_pred = inv_boxcox(y_pred, 0.3)
        y_mean=np.mean(y[holdout_id])
        RSE=np.sum((np.log(y_pred)-np.log(y[holdout_id]))**2)
        MSE=RSE/len(holdout_id)
        RMSE=np.sqrt(MSE)
        RMSE_list.append(RMSE)
    return RMSE_list

## Train Test Split

In [5]:
x_tr, x_val, y_tr, y_val = train_test_split(X, yt, test_size=0.2, random_state=1)

## Model 1: Ridge 

In [6]:
ridge = Ridge(normalize=True, alpha=0.049090909090909095)

In [7]:
print(f"{np.mean(cv_rmse(ridge))} & {np.std(cv_rmse(ridge))}")

0.11739002014532281 & 0.010631679159506977


## Model 2: Lasso 

In [8]:
lasso = Lasso(normalize=True, alpha=0.002454545454545455)

In [9]:
np.mean(cv_rmse(lasso))

0.1141366509262538

## Model 3: Elastic Net
(This is essentially the same as Lasso)

In [10]:
net = ElasticNet(alpha=0.002454545454545455, l1_ratio=1.0)

In [11]:
np.mean(cv_rmse(net))

0.11800127938130314

## Model 4: CatBoost

In [12]:
catB = CatBoostRegressor(iterations=3000)

In [13]:
np.mean(cv_rmse(catB))

Learning rate set to 0.017396
0:	learn: 14.7691469	total: 74.8ms	remaining: 3m 44s
1:	learn: 14.5880851	total: 79.2ms	remaining: 1m 58s
2:	learn: 14.4188203	total: 83ms	remaining: 1m 22s
3:	learn: 14.2472070	total: 86.2ms	remaining: 1m 4s
4:	learn: 14.0937298	total: 89.1ms	remaining: 53.4s
5:	learn: 13.9351549	total: 91.7ms	remaining: 45.8s
6:	learn: 13.7972010	total: 94.3ms	remaining: 40.3s
7:	learn: 13.6446048	total: 97.4ms	remaining: 36.4s
8:	learn: 13.5040481	total: 100ms	remaining: 33.3s
9:	learn: 13.3606378	total: 102ms	remaining: 30.6s
10:	learn: 13.2084976	total: 105ms	remaining: 28.4s
11:	learn: 13.0725660	total: 107ms	remaining: 26.7s
12:	learn: 12.9336183	total: 109ms	remaining: 25.1s
13:	learn: 12.7942577	total: 112ms	remaining: 23.8s
14:	learn: 12.6512209	total: 114ms	remaining: 22.7s
15:	learn: 12.5130767	total: 116ms	remaining: 21.7s
16:	learn: 12.3756976	total: 119ms	remaining: 20.8s
17:	learn: 12.2434636	total: 121ms	remaining: 20s
18:	learn: 12.1084139	total: 123ms	re

165:	learn: 5.0283357	total: 555ms	remaining: 9.47s
166:	learn: 5.0125384	total: 558ms	remaining: 9.46s
167:	learn: 4.9987428	total: 561ms	remaining: 9.46s
168:	learn: 4.9855435	total: 564ms	remaining: 9.45s
169:	learn: 4.9709870	total: 568ms	remaining: 9.45s
170:	learn: 4.9581157	total: 571ms	remaining: 9.45s
171:	learn: 4.9480694	total: 574ms	remaining: 9.45s
172:	learn: 4.9359120	total: 579ms	remaining: 9.46s
173:	learn: 4.9243770	total: 583ms	remaining: 9.46s
174:	learn: 4.9092238	total: 585ms	remaining: 9.45s
175:	learn: 4.8977968	total: 587ms	remaining: 9.43s
176:	learn: 4.8879437	total: 590ms	remaining: 9.41s
177:	learn: 4.8756713	total: 592ms	remaining: 9.39s
178:	learn: 4.8633698	total: 595ms	remaining: 9.38s
179:	learn: 4.8510145	total: 597ms	remaining: 9.36s
180:	learn: 4.8381771	total: 600ms	remaining: 9.34s
181:	learn: 4.8271581	total: 602ms	remaining: 9.32s
182:	learn: 4.8155801	total: 605ms	remaining: 9.32s
183:	learn: 4.8043175	total: 608ms	remaining: 9.3s
184:	learn: 4

384:	learn: 3.6840152	total: 1.12s	remaining: 7.61s
385:	learn: 3.6825460	total: 1.12s	remaining: 7.6s
386:	learn: 3.6806188	total: 1.12s	remaining: 7.59s
387:	learn: 3.6776720	total: 1.13s	remaining: 7.59s
388:	learn: 3.6758511	total: 1.13s	remaining: 7.6s
389:	learn: 3.6728498	total: 1.14s	remaining: 7.64s
390:	learn: 3.6707949	total: 1.15s	remaining: 7.64s
391:	learn: 3.6667798	total: 1.15s	remaining: 7.65s
392:	learn: 3.6628152	total: 1.15s	remaining: 7.66s
393:	learn: 3.6608557	total: 1.16s	remaining: 7.66s
394:	learn: 3.6579158	total: 1.16s	remaining: 7.65s
395:	learn: 3.6550199	total: 1.16s	remaining: 7.64s
396:	learn: 3.6524384	total: 1.17s	remaining: 7.64s
397:	learn: 3.6503412	total: 1.17s	remaining: 7.64s
398:	learn: 3.6467417	total: 1.17s	remaining: 7.63s
399:	learn: 3.6433522	total: 1.17s	remaining: 7.62s
400:	learn: 3.6406849	total: 1.18s	remaining: 7.62s
401:	learn: 3.6369023	total: 1.18s	remaining: 7.61s
402:	learn: 3.6338151	total: 1.18s	remaining: 7.61s
403:	learn: 3.

621:	learn: 3.0729901	total: 1.69s	remaining: 6.45s
622:	learn: 3.0709581	total: 1.69s	remaining: 6.45s
623:	learn: 3.0688625	total: 1.69s	remaining: 6.45s
624:	learn: 3.0662062	total: 1.7s	remaining: 6.45s
625:	learn: 3.0653224	total: 1.7s	remaining: 6.45s
626:	learn: 3.0634701	total: 1.7s	remaining: 6.45s
627:	learn: 3.0601891	total: 1.71s	remaining: 6.44s
628:	learn: 3.0593486	total: 1.71s	remaining: 6.45s
629:	learn: 3.0576674	total: 1.71s	remaining: 6.44s
630:	learn: 3.0558374	total: 1.71s	remaining: 6.43s
631:	learn: 3.0538940	total: 1.72s	remaining: 6.43s
632:	learn: 3.0530487	total: 1.72s	remaining: 6.43s
633:	learn: 3.0508998	total: 1.72s	remaining: 6.42s
634:	learn: 3.0470823	total: 1.72s	remaining: 6.42s
635:	learn: 3.0443571	total: 1.73s	remaining: 6.41s
636:	learn: 3.0413942	total: 1.73s	remaining: 6.41s
637:	learn: 3.0394277	total: 1.73s	remaining: 6.4s
638:	learn: 3.0363221	total: 1.73s	remaining: 6.4s
639:	learn: 3.0334540	total: 1.73s	remaining: 6.39s
640:	learn: 3.030

830:	learn: 2.6487366	total: 2.26s	remaining: 5.89s
831:	learn: 2.6475859	total: 2.26s	remaining: 5.89s
832:	learn: 2.6463978	total: 2.26s	remaining: 5.89s
833:	learn: 2.6447063	total: 2.27s	remaining: 5.89s
834:	learn: 2.6428425	total: 2.27s	remaining: 5.89s
835:	learn: 2.6410655	total: 2.27s	remaining: 5.89s
836:	learn: 2.6393877	total: 2.28s	remaining: 5.89s
837:	learn: 2.6377601	total: 2.28s	remaining: 5.89s
838:	learn: 2.6353473	total: 2.28s	remaining: 5.88s
839:	learn: 2.6330647	total: 2.29s	remaining: 5.88s
840:	learn: 2.6312460	total: 2.29s	remaining: 5.88s
841:	learn: 2.6293893	total: 2.29s	remaining: 5.88s
842:	learn: 2.6272841	total: 2.3s	remaining: 5.88s
843:	learn: 2.6257996	total: 2.3s	remaining: 5.88s
844:	learn: 2.6245697	total: 2.3s	remaining: 5.87s
845:	learn: 2.6226584	total: 2.31s	remaining: 5.87s
846:	learn: 2.6201454	total: 2.31s	remaining: 5.87s
847:	learn: 2.6185058	total: 2.31s	remaining: 5.87s
848:	learn: 2.6171066	total: 2.32s	remaining: 5.87s
849:	learn: 2.6

...

2306:	learn: 1.1630265	total: 7.22s	remaining: 2.17s
2307:	learn: 1.1623629	total: 7.23s	remaining: 2.17s
2308:	learn: 1.1616591	total: 7.23s	remaining: 2.16s
2309:	learn: 1.1610346	total: 7.23s	remaining: 2.16s
2310:	learn: 1.1607438	total: 7.24s	remaining: 2.16s
2311:	learn: 1.1599489	total: 7.24s	remaining: 2.15s
2312:	learn: 1.1593967	total: 7.25s	remaining: 2.15s
2313:	learn: 1.1586097	total: 7.25s	remaining: 2.15s
2314:	learn: 1.1580249	total: 7.25s	remaining: 2.15s
2315:	learn: 1.1574678	total: 7.25s	remaining: 2.14s
2316:	learn: 1.1567334	total: 7.26s	remaining: 2.14s
2317:	learn: 1.1564711	total: 7.26s	remaining: 2.14s
2318:	learn: 1.1558094	total: 7.26s	remaining: 2.13s
2319:	learn: 1.1552117	total: 7.26s	remaining: 2.13s
2320:	learn: 1.1547197	total: 7.27s	remaining: 2.13s
2321:	learn: 1.1541525	total: 7.27s	remaining: 2.12s
2322:	learn: 1.1535833	total: 7.27s	remaining: 2.12s
2323:	learn: 1.1527782	total: 7.28s	remaining: 2.12s
2324:	learn: 1.1520670	total: 7.28s	remaining:

2511:	learn: 1.0591347	total: 7.8s	remaining: 1.51s
2512:	learn: 1.0585232	total: 7.8s	remaining: 1.51s
2513:	learn: 1.0580385	total: 7.8s	remaining: 1.51s
2514:	learn: 1.0576812	total: 7.81s	remaining: 1.5s
2515:	learn: 1.0571682	total: 7.81s	remaining: 1.5s
2516:	learn: 1.0568755	total: 7.82s	remaining: 1.5s
2517:	learn: 1.0564663	total: 7.82s	remaining: 1.5s
2518:	learn: 1.0560883	total: 7.82s	remaining: 1.49s
2519:	learn: 1.0557229	total: 7.83s	remaining: 1.49s
2520:	learn: 1.0549980	total: 7.83s	remaining: 1.49s
2521:	learn: 1.0546168	total: 7.83s	remaining: 1.48s
2522:	learn: 1.0542100	total: 7.83s	remaining: 1.48s
2523:	learn: 1.0538286	total: 7.84s	remaining: 1.48s
2524:	learn: 1.0533803	total: 7.84s	remaining: 1.47s
2525:	learn: 1.0529908	total: 7.84s	remaining: 1.47s
2526:	learn: 1.0525593	total: 7.84s	remaining: 1.47s
2527:	learn: 1.0520559	total: 7.85s	remaining: 1.47s
2528:	learn: 1.0514420	total: 7.85s	remaining: 1.46s
2529:	learn: 1.0507987	total: 7.85s	remaining: 1.46s


2724:	learn: 0.9702953	total: 8.37s	remaining: 844ms
2725:	learn: 0.9697178	total: 8.37s	remaining: 841ms
2726:	learn: 0.9694150	total: 8.37s	remaining: 838ms
2727:	learn: 0.9688886	total: 8.38s	remaining: 835ms
2728:	learn: 0.9686374	total: 8.38s	remaining: 832ms
2729:	learn: 0.9679406	total: 8.38s	remaining: 829ms
2730:	learn: 0.9674341	total: 8.39s	remaining: 826ms
2731:	learn: 0.9671164	total: 8.39s	remaining: 823ms
2732:	learn: 0.9667515	total: 8.39s	remaining: 820ms
2733:	learn: 0.9663231	total: 8.4s	remaining: 817ms
2734:	learn: 0.9657868	total: 8.4s	remaining: 814ms
2735:	learn: 0.9655028	total: 8.4s	remaining: 811ms
2736:	learn: 0.9652636	total: 8.4s	remaining: 808ms
2737:	learn: 0.9648247	total: 8.41s	remaining: 805ms
2738:	learn: 0.9644416	total: 8.41s	remaining: 801ms
2739:	learn: 0.9641925	total: 8.41s	remaining: 798ms
2740:	learn: 0.9638999	total: 8.41s	remaining: 795ms
2741:	learn: 0.9634306	total: 8.42s	remaining: 792ms
2742:	learn: 0.9632209	total: 8.42s	remaining: 789

2933:	learn: 0.8877874	total: 8.93s	remaining: 201ms
2934:	learn: 0.8874947	total: 8.94s	remaining: 198ms
2935:	learn: 0.8871631	total: 8.94s	remaining: 195ms
2936:	learn: 0.8868813	total: 8.94s	remaining: 192ms
2937:	learn: 0.8866857	total: 8.95s	remaining: 189ms
2938:	learn: 0.8864614	total: 8.95s	remaining: 186ms
2939:	learn: 0.8859907	total: 8.96s	remaining: 183ms
2940:	learn: 0.8854630	total: 8.96s	remaining: 180ms
2941:	learn: 0.8850983	total: 8.96s	remaining: 177ms
2942:	learn: 0.8846789	total: 8.97s	remaining: 174ms
2943:	learn: 0.8842927	total: 8.97s	remaining: 171ms
2944:	learn: 0.8837474	total: 8.97s	remaining: 168ms
2945:	learn: 0.8836394	total: 8.97s	remaining: 164ms
2946:	learn: 0.8829966	total: 8.98s	remaining: 161ms
2947:	learn: 0.8826009	total: 8.98s	remaining: 158ms
2948:	learn: 0.8820552	total: 8.98s	remaining: 155ms
2949:	learn: 0.8816520	total: 8.99s	remaining: 152ms
2950:	learn: 0.8813775	total: 8.99s	remaining: 149ms
2951:	learn: 0.8810560	total: 8.99s	remaining:

0.11678353034175341

## Model 5: Gradient Boosting

In [14]:
gb = GradientBoostingRegressor(n_estimators = 4650, learning_rate = 0.04,
                                   max_depth = 2, max_features = 'sqrt',
                                   min_samples_leaf = 4, min_samples_split = 34, 
                                   loss = 'huber', random_state = 1)

0.11426536361076811

In [15]:
np.mean(cv_rmse(gb))

0.11426536361076811

## Model 5: XGBoost

In [16]:
xgboost = xgb.XGBRegressor(
    learning_rate =0.0492,
    n_estimators=2000,
    max_depth=2,
    min_child_weight=4,
    gamma=1.5789473684210527,
    subsample=0.8125,
    colsample_bytree=0.35486333333333336,
    random_state = 1,
    objective = "reg:squarederror")

In [17]:
np.mean(cv_rmse(xgboost))

0.11853573881625416

## LightGBM

In [21]:
lightGBM = lgb.LGBMRegressor(objective = 'regression',
                         num_leaves = 5,
                         learning_rate = 0.05,
                         n_estimators = 1620,
                         max_bin = 55,
                         bagging_fraction = 0.889,
                         bagging_freq = 7,
                         feature_fraction = 0.23157894736842105,
                         feature_fraction_seed = 9,
                         bagging_seed = 9,
                         random_state = 1,
                         min_data_in_leaf = 7,
                         min_sum_hessian_in_leaf = 7)

In [22]:
np.mean(cv_rmse(lightGBM))

0.11855162941130626

# Model Emsembling

## Simple Averaging Model

In [23]:
class AveragingModels(BaseEstimator, RegressorMixin, TransformerMixin):
    def __init__(self, models):
        self.models = models
        
    # we define clones of the original models to fit the data in
    def fit(self, X, y):
        self.models_ = [clone(x) for x in self.models]
        
        # Train cloned base models
        for model in self.models_:
            model.fit(X, y)

        return self
    
    #Now we do the predictions for cloned models and average them
    def predict(self, X):
        predictions = np.column_stack([
            model.predict(X) for model in self.models_
        ])
        return np.mean(predictions, axis=1)   


In [24]:
simple_stack_model = AveragingModels(models = (lasso, net, catB, gb, xgboost, lightGBM))
np.mean(cv_rmse(simple_stack_model))

Learning rate set to 0.017396
0:	learn: 14.7691469	total: 12.2ms	remaining: 36.5s
1:	learn: 14.5880851	total: 15.2ms	remaining: 22.8s
2:	learn: 14.4188203	total: 18.1ms	remaining: 18.1s
3:	learn: 14.2472070	total: 21.1ms	remaining: 15.8s
4:	learn: 14.0937298	total: 24ms	remaining: 14.4s
5:	learn: 13.9351549	total: 27.4ms	remaining: 13.7s
6:	learn: 13.7972010	total: 30.2ms	remaining: 12.9s
7:	learn: 13.6446048	total: 33ms	remaining: 12.4s
8:	learn: 13.5040481	total: 35.8ms	remaining: 11.9s
9:	learn: 13.3606378	total: 38.6ms	remaining: 11.5s
10:	learn: 13.2084976	total: 41.4ms	remaining: 11.2s
11:	learn: 13.0725660	total: 44.7ms	remaining: 11.1s
12:	learn: 12.9336183	total: 47.7ms	remaining: 11s
13:	learn: 12.7942577	total: 50.6ms	remaining: 10.8s
14:	learn: 12.6512209	total: 53.4ms	remaining: 10.6s
15:	learn: 12.5130767	total: 56.3ms	remaining: 10.5s
16:	learn: 12.3756976	total: 60.2ms	remaining: 10.6s
17:	learn: 12.2434636	total: 63.1ms	remaining: 10.5s
18:	learn: 12.1084139	total: 66.

165:	learn: 5.0283357	total: 560ms	remaining: 9.55s
166:	learn: 5.0125384	total: 565ms	remaining: 9.58s
167:	learn: 4.9987428	total: 569ms	remaining: 9.59s
168:	learn: 4.9855435	total: 573ms	remaining: 9.6s
169:	learn: 4.9709870	total: 577ms	remaining: 9.61s
170:	learn: 4.9581157	total: 581ms	remaining: 9.61s
171:	learn: 4.9480694	total: 585ms	remaining: 9.61s
172:	learn: 4.9359120	total: 588ms	remaining: 9.61s
173:	learn: 4.9243770	total: 592ms	remaining: 9.61s
174:	learn: 4.9092238	total: 595ms	remaining: 9.61s
175:	learn: 4.8977968	total: 599ms	remaining: 9.61s
176:	learn: 4.8879437	total: 603ms	remaining: 9.61s
177:	learn: 4.8756713	total: 606ms	remaining: 9.61s
178:	learn: 4.8633698	total: 610ms	remaining: 9.62s
179:	learn: 4.8510145	total: 615ms	remaining: 9.63s
180:	learn: 4.8381771	total: 620ms	remaining: 9.66s
181:	learn: 4.8271581	total: 624ms	remaining: 9.66s
182:	learn: 4.8155801	total: 628ms	remaining: 9.66s
183:	learn: 4.8043175	total: 632ms	remaining: 9.68s
184:	learn: 4

330:	learn: 3.8750511	total: 1.13s	remaining: 9.13s
331:	learn: 3.8709569	total: 1.14s	remaining: 9.13s
332:	learn: 3.8654790	total: 1.14s	remaining: 9.12s
333:	learn: 3.8617140	total: 1.14s	remaining: 9.11s
334:	learn: 3.8578212	total: 1.14s	remaining: 9.11s
335:	learn: 3.8536837	total: 1.15s	remaining: 9.1s
336:	learn: 3.8489738	total: 1.15s	remaining: 9.1s
337:	learn: 3.8469067	total: 1.16s	remaining: 9.1s
338:	learn: 3.8428884	total: 1.16s	remaining: 9.1s
339:	learn: 3.8386627	total: 1.16s	remaining: 9.09s
340:	learn: 3.8332446	total: 1.16s	remaining: 9.08s
341:	learn: 3.8302734	total: 1.17s	remaining: 9.07s
342:	learn: 3.8271072	total: 1.17s	remaining: 9.06s
343:	learn: 3.8232364	total: 1.17s	remaining: 9.05s
344:	learn: 3.8193513	total: 1.18s	remaining: 9.05s
345:	learn: 3.8151678	total: 1.18s	remaining: 9.04s
346:	learn: 3.8129136	total: 1.18s	remaining: 9.03s
347:	learn: 3.8097380	total: 1.18s	remaining: 9.02s
348:	learn: 3.8064145	total: 1.19s	remaining: 9.01s
349:	learn: 3.80

527:	learn: 3.3028308	total: 1.71s	remaining: 7.99s
528:	learn: 3.3010493	total: 1.71s	remaining: 7.99s
529:	learn: 3.2985359	total: 1.72s	remaining: 7.99s
530:	learn: 3.2954649	total: 1.72s	remaining: 8s
531:	learn: 3.2937882	total: 1.72s	remaining: 8s
532:	learn: 3.2902198	total: 1.73s	remaining: 8s
533:	learn: 3.2874366	total: 1.73s	remaining: 8s
534:	learn: 3.2862061	total: 1.73s	remaining: 7.99s
535:	learn: 3.2825933	total: 1.74s	remaining: 7.99s
536:	learn: 3.2797377	total: 1.74s	remaining: 7.98s
537:	learn: 3.2780622	total: 1.74s	remaining: 7.98s
538:	learn: 3.2768112	total: 1.75s	remaining: 7.97s
539:	learn: 3.2747315	total: 1.75s	remaining: 7.97s
540:	learn: 3.2723893	total: 1.75s	remaining: 7.96s
541:	learn: 3.2712940	total: 1.75s	remaining: 7.96s
542:	learn: 3.2697260	total: 1.76s	remaining: 7.95s
543:	learn: 3.2676090	total: 1.76s	remaining: 7.95s
544:	learn: 3.2651225	total: 1.76s	remaining: 7.94s
545:	learn: 3.2622399	total: 1.76s	remaining: 7.94s
546:	learn: 3.2610328	to

737:	learn: 2.8241677	total: 2.28s	remaining: 7s
738:	learn: 2.8223542	total: 2.29s	remaining: 7s
739:	learn: 2.8202853	total: 2.29s	remaining: 6.99s
740:	learn: 2.8183966	total: 2.29s	remaining: 6.99s
741:	learn: 2.8158979	total: 2.3s	remaining: 6.99s
742:	learn: 2.8138537	total: 2.3s	remaining: 6.99s
743:	learn: 2.8118461	total: 2.3s	remaining: 6.98s
744:	learn: 2.8098471	total: 2.31s	remaining: 6.98s
745:	learn: 2.8079970	total: 2.31s	remaining: 6.98s
746:	learn: 2.8061799	total: 2.31s	remaining: 6.97s
747:	learn: 2.8042212	total: 2.31s	remaining: 6.97s
748:	learn: 2.8023162	total: 2.32s	remaining: 6.96s
749:	learn: 2.8002708	total: 2.32s	remaining: 6.96s
750:	learn: 2.7980681	total: 2.32s	remaining: 6.95s
751:	learn: 2.7957751	total: 2.32s	remaining: 6.94s
752:	learn: 2.7941165	total: 2.32s	remaining: 6.94s
753:	learn: 2.7928043	total: 2.33s	remaining: 6.93s
754:	learn: 2.7916362	total: 2.33s	remaining: 6.93s
755:	learn: 2.7891688	total: 2.33s	remaining: 6.92s
756:	learn: 2.7872630

...

2199:	learn: 1.2233957	total: 5.46s	remaining: 1.99s
2200:	learn: 1.2227713	total: 5.47s	remaining: 1.98s
2201:	learn: 1.2219114	total: 5.47s	remaining: 1.98s
2202:	learn: 1.2213998	total: 5.47s	remaining: 1.98s
2203:	learn: 1.2207550	total: 5.48s	remaining: 1.98s
2204:	learn: 1.2200617	total: 5.48s	remaining: 1.98s
2205:	learn: 1.2193870	total: 5.48s	remaining: 1.97s
2206:	learn: 1.2188790	total: 5.49s	remaining: 1.97s
2207:	learn: 1.2184677	total: 5.49s	remaining: 1.97s
2208:	learn: 1.2177462	total: 5.49s	remaining: 1.97s
2209:	learn: 1.2169385	total: 5.5s	remaining: 1.97s
2210:	learn: 1.2166119	total: 5.5s	remaining: 1.96s
2211:	learn: 1.2159971	total: 5.5s	remaining: 1.96s
2212:	learn: 1.2159336	total: 5.51s	remaining: 1.96s
2213:	learn: 1.2151800	total: 5.51s	remaining: 1.96s
2214:	learn: 1.2143755	total: 5.51s	remaining: 1.95s
2215:	learn: 1.2140699	total: 5.52s	remaining: 1.95s
2216:	learn: 1.2139992	total: 5.52s	remaining: 1.95s
2217:	learn: 1.2137775	total: 5.52s	remaining: 1.

2396:	learn: 1.1174301	total: 6.03s	remaining: 1.52s
2397:	learn: 1.1169754	total: 6.03s	remaining: 1.51s
2398:	learn: 1.1163633	total: 6.04s	remaining: 1.51s
2399:	learn: 1.1157097	total: 6.04s	remaining: 1.51s
2400:	learn: 1.1152321	total: 6.04s	remaining: 1.51s
2401:	learn: 1.1145027	total: 6.04s	remaining: 1.5s
2402:	learn: 1.1138972	total: 6.05s	remaining: 1.5s
2403:	learn: 1.1132122	total: 6.05s	remaining: 1.5s
2404:	learn: 1.1126255	total: 6.05s	remaining: 1.5s
2405:	learn: 1.1120311	total: 6.05s	remaining: 1.49s
2406:	learn: 1.1114814	total: 6.06s	remaining: 1.49s
2407:	learn: 1.1107782	total: 6.06s	remaining: 1.49s
2408:	learn: 1.1100255	total: 6.06s	remaining: 1.49s
2409:	learn: 1.1090743	total: 6.06s	remaining: 1.48s
2410:	learn: 1.1082781	total: 6.07s	remaining: 1.48s
2411:	learn: 1.1078223	total: 6.07s	remaining: 1.48s
2412:	learn: 1.1077526	total: 6.07s	remaining: 1.48s
2413:	learn: 1.1070455	total: 6.08s	remaining: 1.47s
2414:	learn: 1.1062863	total: 6.08s	remaining: 1.4

2591:	learn: 1.0227925	total: 6.6s	remaining: 1.04s
2592:	learn: 1.0223421	total: 6.6s	remaining: 1.04s
2593:	learn: 1.0221052	total: 6.6s	remaining: 1.03s
2594:	learn: 1.0216966	total: 6.61s	remaining: 1.03s
2595:	learn: 1.0212120	total: 6.61s	remaining: 1.03s
2596:	learn: 1.0205738	total: 6.61s	remaining: 1.02s
2597:	learn: 1.0203422	total: 6.61s	remaining: 1.02s
2598:	learn: 1.0200219	total: 6.62s	remaining: 1.02s
2599:	learn: 1.0197849	total: 6.62s	remaining: 1.02s
2600:	learn: 1.0193896	total: 6.62s	remaining: 1.01s
2601:	learn: 1.0189790	total: 6.62s	remaining: 1.01s
2602:	learn: 1.0183757	total: 6.63s	remaining: 1.01s
2603:	learn: 1.0175908	total: 6.63s	remaining: 1.01s
2604:	learn: 1.0173477	total: 6.63s	remaining: 1s
2605:	learn: 1.0169333	total: 6.63s	remaining: 1s
2606:	learn: 1.0163889	total: 6.64s	remaining: 1s
2607:	learn: 1.0158320	total: 6.64s	remaining: 998ms
2608:	learn: 1.0152604	total: 6.64s	remaining: 995ms
2609:	learn: 1.0149237	total: 6.64s	remaining: 993ms
2610:

2798:	learn: 0.9411475	total: 7.17s	remaining: 515ms
2799:	learn: 0.9411073	total: 7.17s	remaining: 512ms
2800:	learn: 0.9406461	total: 7.17s	remaining: 509ms
2801:	learn: 0.9401256	total: 7.17s	remaining: 507ms
2802:	learn: 0.9398482	total: 7.18s	remaining: 504ms
2803:	learn: 0.9394074	total: 7.18s	remaining: 502ms
2804:	learn: 0.9388931	total: 7.18s	remaining: 499ms
2805:	learn: 0.9385000	total: 7.18s	remaining: 497ms
2806:	learn: 0.9381335	total: 7.19s	remaining: 494ms
2807:	learn: 0.9375829	total: 7.19s	remaining: 492ms
2808:	learn: 0.9369837	total: 7.19s	remaining: 489ms
2809:	learn: 0.9366254	total: 7.2s	remaining: 487ms
2810:	learn: 0.9359155	total: 7.2s	remaining: 484ms
2811:	learn: 0.9354858	total: 7.2s	remaining: 481ms
2812:	learn: 0.9349929	total: 7.2s	remaining: 479ms
2813:	learn: 0.9344615	total: 7.21s	remaining: 476ms
2814:	learn: 0.9339028	total: 7.21s	remaining: 474ms
2815:	learn: 0.9335878	total: 7.21s	remaining: 471ms
2816:	learn: 0.9331534	total: 7.22s	remaining: 469

0.11090189360842054

In [25]:
simple_stack_model.fit(x_tr,y_tr)
prediction=simple_stack_model.predict(test)
prediction=inv_boxcox(prediction, 0.3)
pred = pd.DataFrame(prediction, columns=['SalePrice'])
ID = test_raw[['Id']]
sub=pd.merge(ID, pred, left_on = ID.index, right_on = pred.index).drop(columns=['key_0'])
sub.to_csv('../Submissions/submission_simpleStacked.csv',index=False)
prediction

Learning rate set to 0.017396
0:	learn: 14.7746805	total: 4.07ms	remaining: 12.2s
1:	learn: 14.5931585	total: 7.03ms	remaining: 10.5s
2:	learn: 14.4182479	total: 10.4ms	remaining: 10.4s
3:	learn: 14.2402500	total: 13.2ms	remaining: 9.91s
4:	learn: 14.0867596	total: 16ms	remaining: 9.61s
5:	learn: 13.9239105	total: 18.9ms	remaining: 9.43s
6:	learn: 13.7771745	total: 21.8ms	remaining: 9.33s
7:	learn: 13.6255168	total: 24.7ms	remaining: 9.23s
8:	learn: 13.4794081	total: 28.5ms	remaining: 9.47s
9:	learn: 13.3370035	total: 31.6ms	remaining: 9.44s
10:	learn: 13.1837939	total: 34.3ms	remaining: 9.31s
11:	learn: 13.0460550	total: 37.1ms	remaining: 9.25s
12:	learn: 12.9055684	total: 40ms	remaining: 9.19s
13:	learn: 12.7630508	total: 42.8ms	remaining: 9.12s
14:	learn: 12.6204645	total: 46.2ms	remaining: 9.18s
15:	learn: 12.4802343	total: 50.2ms	remaining: 9.37s
16:	learn: 12.3436662	total: 53.1ms	remaining: 9.32s
17:	learn: 12.2119089	total: 55.9ms	remaining: 9.26s
18:	learn: 12.0855505	total: 5

171:	learn: 4.9369612	total: 567ms	remaining: 9.33s
172:	learn: 4.9228003	total: 571ms	remaining: 9.33s
173:	learn: 4.9121339	total: 575ms	remaining: 9.34s
174:	learn: 4.8997494	total: 579ms	remaining: 9.34s
175:	learn: 4.8868814	total: 582ms	remaining: 9.34s
176:	learn: 4.8762701	total: 586ms	remaining: 9.35s
177:	learn: 4.8650673	total: 590ms	remaining: 9.35s
178:	learn: 4.8533249	total: 593ms	remaining: 9.35s
179:	learn: 4.8424503	total: 597ms	remaining: 9.36s
180:	learn: 4.8298397	total: 600ms	remaining: 9.35s
181:	learn: 4.8207911	total: 604ms	remaining: 9.35s
182:	learn: 4.8103734	total: 609ms	remaining: 9.37s
183:	learn: 4.7994674	total: 612ms	remaining: 9.37s
184:	learn: 4.7893472	total: 615ms	remaining: 9.37s
185:	learn: 4.7787052	total: 619ms	remaining: 9.37s
186:	learn: 4.7671600	total: 623ms	remaining: 9.37s
187:	learn: 4.7591639	total: 626ms	remaining: 9.36s
188:	learn: 4.7502383	total: 630ms	remaining: 9.37s
189:	learn: 4.7409907	total: 634ms	remaining: 9.37s
190:	learn: 

372:	learn: 3.7070254	total: 1.14s	remaining: 8s
373:	learn: 3.7048258	total: 1.14s	remaining: 8.01s
374:	learn: 3.7010258	total: 1.14s	remaining: 8.01s
375:	learn: 3.6972511	total: 1.15s	remaining: 8.01s
376:	learn: 3.6946557	total: 1.15s	remaining: 8.02s
377:	learn: 3.6901142	total: 1.16s	remaining: 8.02s
378:	learn: 3.6870241	total: 1.16s	remaining: 8.02s
379:	learn: 3.6832713	total: 1.16s	remaining: 8.02s
380:	learn: 3.6805069	total: 1.17s	remaining: 8.01s
381:	learn: 3.6776524	total: 1.17s	remaining: 8.01s
382:	learn: 3.6734182	total: 1.17s	remaining: 8s
383:	learn: 3.6706424	total: 1.17s	remaining: 8s
384:	learn: 3.6686727	total: 1.18s	remaining: 7.99s
385:	learn: 3.6659806	total: 1.18s	remaining: 7.99s
386:	learn: 3.6633206	total: 1.18s	remaining: 7.98s
387:	learn: 3.6596583	total: 1.18s	remaining: 7.97s
388:	learn: 3.6573313	total: 1.19s	remaining: 7.97s
389:	learn: 3.6551929	total: 1.19s	remaining: 7.96s
390:	learn: 3.6508303	total: 1.19s	remaining: 7.96s
391:	learn: 3.6479772

594:	learn: 3.1118454	total: 1.7s	remaining: 6.88s
595:	learn: 3.1102210	total: 1.7s	remaining: 6.87s
596:	learn: 3.1085911	total: 1.71s	remaining: 6.87s
597:	learn: 3.1071234	total: 1.71s	remaining: 6.87s
598:	learn: 3.1056311	total: 1.71s	remaining: 6.87s
599:	learn: 3.1045432	total: 1.72s	remaining: 6.87s
600:	learn: 3.1030211	total: 1.72s	remaining: 6.87s
601:	learn: 3.1000743	total: 1.72s	remaining: 6.86s
602:	learn: 3.0974892	total: 1.73s	remaining: 6.86s
603:	learn: 3.0939816	total: 1.73s	remaining: 6.85s
604:	learn: 3.0919502	total: 1.73s	remaining: 6.85s
605:	learn: 3.0891806	total: 1.73s	remaining: 6.84s
606:	learn: 3.0875189	total: 1.73s	remaining: 6.84s
607:	learn: 3.0865685	total: 1.74s	remaining: 6.83s
608:	learn: 3.0840404	total: 1.74s	remaining: 6.83s
609:	learn: 3.0808378	total: 1.74s	remaining: 6.82s
610:	learn: 3.0788812	total: 1.74s	remaining: 6.82s
611:	learn: 3.0757390	total: 1.75s	remaining: 6.81s
612:	learn: 3.0727736	total: 1.75s	remaining: 6.81s
613:	learn: 3.

753:	learn: 2.7752315	total: 2.08s	remaining: 6.2s
754:	learn: 2.7727545	total: 2.08s	remaining: 6.2s
755:	learn: 2.7702538	total: 2.09s	remaining: 6.19s
756:	learn: 2.7682140	total: 2.09s	remaining: 6.19s
757:	learn: 2.7655283	total: 2.09s	remaining: 6.19s
758:	learn: 2.7632204	total: 2.1s	remaining: 6.19s
759:	learn: 2.7608535	total: 2.1s	remaining: 6.18s
760:	learn: 2.7592779	total: 2.1s	remaining: 6.18s
761:	learn: 2.7575099	total: 2.1s	remaining: 6.18s
762:	learn: 2.7546284	total: 2.11s	remaining: 6.18s
763:	learn: 2.7524724	total: 2.11s	remaining: 6.18s
764:	learn: 2.7518047	total: 2.11s	remaining: 6.17s
765:	learn: 2.7494042	total: 2.12s	remaining: 6.17s
766:	learn: 2.7464896	total: 2.12s	remaining: 6.17s
767:	learn: 2.7443147	total: 2.12s	remaining: 6.16s
768:	learn: 2.7427116	total: 2.12s	remaining: 6.16s
769:	learn: 2.7408360	total: 2.12s	remaining: 6.15s
770:	learn: 2.7380627	total: 2.13s	remaining: 6.15s
771:	learn: 2.7365397	total: 2.13s	remaining: 6.14s
772:	learn: 2.7339

...

2428:	learn: 1.1740271	total: 6.05s	remaining: 1.42s
2429:	learn: 1.1733031	total: 6.06s	remaining: 1.42s
2430:	learn: 1.1730149	total: 6.06s	remaining: 1.42s
2431:	learn: 1.1723728	total: 6.06s	remaining: 1.42s
2432:	learn: 1.1718480	total: 6.07s	remaining: 1.41s
2433:	learn: 1.1711372	total: 6.07s	remaining: 1.41s
2434:	learn: 1.1707878	total: 6.08s	remaining: 1.41s
2435:	learn: 1.1697477	total: 6.08s	remaining: 1.41s
2436:	learn: 1.1694668	total: 6.08s	remaining: 1.41s
2437:	learn: 1.1691881	total: 6.09s	remaining: 1.4s
2438:	learn: 1.1687657	total: 6.09s	remaining: 1.4s
2439:	learn: 1.1682524	total: 6.09s	remaining: 1.4s
2440:	learn: 1.1674158	total: 6.09s	remaining: 1.4s
2441:	learn: 1.1671600	total: 6.1s	remaining: 1.39s
2442:	learn: 1.1665955	total: 6.1s	remaining: 1.39s
2443:	learn: 1.1662853	total: 6.11s	remaining: 1.39s
2444:	learn: 1.1659044	total: 6.11s	remaining: 1.39s
2445:	learn: 1.1653694	total: 6.11s	remaining: 1.38s
2446:	learn: 1.1652321	total: 6.12s	remaining: 1.38s

2608:	learn: 1.0853018	total: 6.63s	remaining: 993ms
2609:	learn: 1.0849426	total: 6.63s	remaining: 991ms
2610:	learn: 1.0847452	total: 6.63s	remaining: 989ms
2611:	learn: 1.0843305	total: 6.64s	remaining: 986ms
2612:	learn: 1.0835397	total: 6.64s	remaining: 984ms
2613:	learn: 1.0830237	total: 6.64s	remaining: 981ms
2614:	learn: 1.0826499	total: 6.65s	remaining: 979ms
2615:	learn: 1.0823596	total: 6.65s	remaining: 976ms
2616:	learn: 1.0819805	total: 6.65s	remaining: 974ms
2617:	learn: 1.0816063	total: 6.66s	remaining: 971ms
2618:	learn: 1.0815007	total: 6.66s	remaining: 969ms
2619:	learn: 1.0810846	total: 6.66s	remaining: 966ms
2620:	learn: 1.0809923	total: 6.67s	remaining: 964ms
2621:	learn: 1.0807080	total: 6.67s	remaining: 962ms
2622:	learn: 1.0798998	total: 6.67s	remaining: 959ms
2623:	learn: 1.0796483	total: 6.68s	remaining: 957ms
2624:	learn: 1.0794386	total: 6.68s	remaining: 954ms
2625:	learn: 1.0789355	total: 6.68s	remaining: 952ms
2626:	learn: 1.0786625	total: 6.69s	remaining:

2800:	learn: 1.0000373	total: 7.2s	remaining: 512ms
2801:	learn: 0.9995837	total: 7.21s	remaining: 509ms
2802:	learn: 0.9993664	total: 7.21s	remaining: 507ms
2803:	learn: 0.9988180	total: 7.21s	remaining: 504ms
2804:	learn: 0.9981752	total: 7.21s	remaining: 502ms
2805:	learn: 0.9975881	total: 7.22s	remaining: 499ms
2806:	learn: 0.9971519	total: 7.22s	remaining: 497ms
2807:	learn: 0.9966215	total: 7.23s	remaining: 494ms
2808:	learn: 0.9964171	total: 7.23s	remaining: 492ms
2809:	learn: 0.9960878	total: 7.23s	remaining: 489ms
2810:	learn: 0.9957521	total: 7.24s	remaining: 487ms
2811:	learn: 0.9955927	total: 7.24s	remaining: 484ms
2812:	learn: 0.9950301	total: 7.24s	remaining: 481ms
2813:	learn: 0.9945695	total: 7.25s	remaining: 479ms
2814:	learn: 0.9942408	total: 7.25s	remaining: 476ms
2815:	learn: 0.9937204	total: 7.25s	remaining: 474ms
2816:	learn: 0.9933312	total: 7.25s	remaining: 471ms
2817:	learn: 0.9929130	total: 7.26s	remaining: 469ms
2818:	learn: 0.9923917	total: 7.26s	remaining: 

2997:	learn: 0.9206856	total: 7.74s	remaining: 5.16ms
2998:	learn: 0.9203350	total: 7.74s	remaining: 2.58ms
2999:	learn: 0.9202787	total: 7.74s	remaining: 0us


array([126233.75174887, 161549.71421658, 187208.5610083 , ...,
       164547.52540017, 123768.87787767, 206341.25838902])

## Stacked (meta_model=lasso)

StackingModels Class Source: https://www.kaggle.com/serigne/stacked-regressions-top-4-on-leaderboard

In [26]:
class StackingAveragedModels(BaseEstimator, RegressorMixin, TransformerMixin):
    def __init__(self, base_models, meta_model, n_folds=5):
        self.base_models = base_models
        self.meta_model = meta_model
        self.n_folds = n_folds
   
    # We again fit the data on clones of the original base models
    # We need the clone because we do not want to 
    # continuously fit and overwrite the original base models.
    def fit(self, X, yt):
        self.base_models_ = [list() for x in self.base_models]
        self.meta_model_ = clone(self.meta_model)
        kfold = KFold(n_splits=self.n_folds, shuffle=True, random_state=1)
        # Train cloned base models then create out-of-fold predictions
        # that are needed to train the cloned meta-model.
        outoffold_pred = np.zeros((X.shape[0], len(self.base_models)))
        for i, model in enumerate(self.base_models):
            for train_id, holdout_id in kfold.split(X, yt):
                instance = clone(model)
                self.base_models_[i].append(instance)
                instance.fit(X.iloc[train_id], yt[train_id])
                y_pred = instance.predict(X.iloc[holdout_id])
                outoffold_pred[holdout_id, i] = y_pred  
        # Now train the cloned  meta-model using the out-of-fold predictions as new feature
        self.meta_model_.fit(outoffold_pred, yt)
        print(self.meta_model_.coef_)
        return self
   
    #Do the predictions of all base models on the test data and use the averaged predictions as 
    #meta-features for the final prediction which is done by the meta-model
    def predict(self, X):
        meta_features = np.column_stack([
            np.column_stack([model.predict(X) for model in base_models]).mean(axis=1)
            for base_models in self.base_models_ ])
        return self.meta_model_.predict(meta_features)

In [27]:
stacked_models = StackingAveragedModels(base_models = (lasso, net, gb, catB, xgboost),
                                                 meta_model = Lasso())
score = cv_rmse(stacked_models)
print(f"Stacked model RMSE Score: {np.mean(score)}")
# lasso, net, gb, xgboost, lightGBM - 0.10995646549877361
# ridge, lasso, net, gb, lightGBM - 0.1098998248584195
# stacked 1: ridge, lasso, net, gb, catB, xgboost - 0.10959475310991433
# stacked 2: lasso, net, gb, catB, xgboost - 0.10958984127519941

Learning rate set to 0.016718
0:	learn: 15.0757193	total: 3.75ms	remaining: 11.3s
1:	learn: 14.9017169	total: 7.05ms	remaining: 10.6s
2:	learn: 14.7428868	total: 9.36ms	remaining: 9.35s
3:	learn: 14.5869497	total: 11.8ms	remaining: 8.87s
4:	learn: 14.4410261	total: 13.8ms	remaining: 8.3s
5:	learn: 14.2882241	total: 16.3ms	remaining: 8.11s
6:	learn: 14.1355208	total: 19ms	remaining: 8.11s
7:	learn: 13.9855183	total: 21.8ms	remaining: 8.15s
8:	learn: 13.8446123	total: 24.4ms	remaining: 8.11s
9:	learn: 13.7058632	total: 26.8ms	remaining: 8.02s
10:	learn: 13.5653655	total: 29.1ms	remaining: 7.9s
11:	learn: 13.4309996	total: 31.4ms	remaining: 7.83s
12:	learn: 13.2865856	total: 34.3ms	remaining: 7.89s
13:	learn: 13.1484096	total: 37.4ms	remaining: 7.97s
14:	learn: 13.0056313	total: 39.9ms	remaining: 7.95s
15:	learn: 12.8762269	total: 42.3ms	remaining: 7.88s
16:	learn: 12.7554671	total: 44.5ms	remaining: 7.81s
17:	learn: 12.6252915	total: 46.7ms	remaining: 7.74s
18:	learn: 12.4981388	total: 4

211:	learn: 4.6349826	total: 563ms	remaining: 7.4s
212:	learn: 4.6277176	total: 566ms	remaining: 7.41s
213:	learn: 4.6160701	total: 569ms	remaining: 7.4s
214:	learn: 4.6055649	total: 572ms	remaining: 7.41s
215:	learn: 4.5962923	total: 575ms	remaining: 7.41s
216:	learn: 4.5840864	total: 577ms	remaining: 7.4s
217:	learn: 4.5763836	total: 580ms	remaining: 7.41s
218:	learn: 4.5659849	total: 584ms	remaining: 7.41s
219:	learn: 4.5568424	total: 587ms	remaining: 7.42s
220:	learn: 4.5453922	total: 589ms	remaining: 7.41s
221:	learn: 4.5374999	total: 592ms	remaining: 7.4s
222:	learn: 4.5295908	total: 594ms	remaining: 7.4s
223:	learn: 4.5212931	total: 597ms	remaining: 7.4s
224:	learn: 4.5122762	total: 601ms	remaining: 7.41s
225:	learn: 4.5050394	total: 604ms	remaining: 7.41s
226:	learn: 4.4977405	total: 607ms	remaining: 7.41s
227:	learn: 4.4907233	total: 610ms	remaining: 7.41s
228:	learn: 4.4808884	total: 612ms	remaining: 7.41s
229:	learn: 4.4723828	total: 616ms	remaining: 7.42s
230:	learn: 4.4662

445:	learn: 3.4739714	total: 1.13s	remaining: 6.46s
446:	learn: 3.4709870	total: 1.13s	remaining: 6.46s
447:	learn: 3.4678429	total: 1.13s	remaining: 6.46s
448:	learn: 3.4647895	total: 1.14s	remaining: 6.45s
449:	learn: 3.4612701	total: 1.14s	remaining: 6.45s
450:	learn: 3.4591933	total: 1.14s	remaining: 6.44s
451:	learn: 3.4567419	total: 1.14s	remaining: 6.44s
452:	learn: 3.4542578	total: 1.15s	remaining: 6.44s
453:	learn: 3.4513613	total: 1.15s	remaining: 6.44s
454:	learn: 3.4463531	total: 1.15s	remaining: 6.43s
455:	learn: 3.4427569	total: 1.15s	remaining: 6.43s
456:	learn: 3.4382551	total: 1.16s	remaining: 6.43s
457:	learn: 3.4335073	total: 1.16s	remaining: 6.43s
458:	learn: 3.4304323	total: 1.16s	remaining: 6.43s
459:	learn: 3.4268655	total: 1.16s	remaining: 6.42s
460:	learn: 3.4230428	total: 1.17s	remaining: 6.42s
461:	learn: 3.4193211	total: 1.17s	remaining: 6.42s
462:	learn: 3.4152064	total: 1.17s	remaining: 6.41s
463:	learn: 3.4129807	total: 1.17s	remaining: 6.41s
464:	learn: 

608:	learn: 3.0233218	total: 1.5s	remaining: 5.91s
609:	learn: 3.0229365	total: 1.51s	remaining: 5.91s
610:	learn: 3.0205399	total: 1.51s	remaining: 5.9s
611:	learn: 3.0195223	total: 1.51s	remaining: 5.9s
612:	learn: 3.0190839	total: 1.51s	remaining: 5.9s
613:	learn: 3.0163233	total: 1.52s	remaining: 5.89s
614:	learn: 3.0153210	total: 1.52s	remaining: 5.89s
615:	learn: 3.0121861	total: 1.52s	remaining: 5.89s
616:	learn: 3.0084439	total: 1.52s	remaining: 5.89s
617:	learn: 3.0049576	total: 1.53s	remaining: 5.89s
618:	learn: 3.0008736	total: 1.53s	remaining: 5.89s
619:	learn: 2.9997817	total: 1.53s	remaining: 5.88s
620:	learn: 2.9964114	total: 1.53s	remaining: 5.88s
621:	learn: 2.9943537	total: 1.54s	remaining: 5.88s
622:	learn: 2.9931762	total: 1.54s	remaining: 5.88s
623:	learn: 2.9900728	total: 1.54s	remaining: 5.87s
624:	learn: 2.9867349	total: 1.54s	remaining: 5.87s
625:	learn: 2.9861289	total: 1.55s	remaining: 5.86s
626:	learn: 2.9831523	total: 1.55s	remaining: 5.86s
627:	learn: 2.98

782:	learn: 2.6251735	total: 1.88s	remaining: 5.33s
783:	learn: 2.6223898	total: 1.89s	remaining: 5.33s
784:	learn: 2.6204914	total: 1.89s	remaining: 5.33s
785:	learn: 2.6178237	total: 1.89s	remaining: 5.33s
786:	learn: 2.6165597	total: 1.89s	remaining: 5.32s
787:	learn: 2.6154284	total: 1.9s	remaining: 5.32s
788:	learn: 2.6138371	total: 1.9s	remaining: 5.32s
789:	learn: 2.6115852	total: 1.9s	remaining: 5.32s
790:	learn: 2.6090187	total: 1.9s	remaining: 5.32s
791:	learn: 2.6076128	total: 1.91s	remaining: 5.32s
792:	learn: 2.6054087	total: 1.91s	remaining: 5.32s
793:	learn: 2.6034976	total: 1.91s	remaining: 5.31s
794:	learn: 2.6007191	total: 1.91s	remaining: 5.31s
795:	learn: 2.5988373	total: 1.92s	remaining: 5.31s
796:	learn: 2.5984559	total: 1.92s	remaining: 5.3s
797:	learn: 2.5960886	total: 1.92s	remaining: 5.3s
798:	learn: 2.5941126	total: 1.92s	remaining: 5.3s
799:	learn: 2.5921143	total: 1.93s	remaining: 5.3s
800:	learn: 2.5897548	total: 1.93s	remaining: 5.29s
801:	learn: 2.587266

...

2201:	learn: 1.1022425	total: 5.51s	remaining: 2s
2202:	learn: 1.1016300	total: 5.51s	remaining: 1.99s
2203:	learn: 1.1009105	total: 5.51s	remaining: 1.99s
2204:	learn: 1.1003539	total: 5.51s	remaining: 1.99s
2205:	learn: 1.0998529	total: 5.51s	remaining: 1.99s
2206:	learn: 1.0992748	total: 5.52s	remaining: 1.98s
2207:	learn: 1.0987442	total: 5.52s	remaining: 1.98s
2208:	learn: 1.0980067	total: 5.52s	remaining: 1.98s
2209:	learn: 1.0974755	total: 5.53s	remaining: 1.98s
2210:	learn: 1.0974291	total: 5.53s	remaining: 1.97s
2211:	learn: 1.0967810	total: 5.53s	remaining: 1.97s
2212:	learn: 1.0967277	total: 5.53s	remaining: 1.97s
2213:	learn: 1.0960708	total: 5.54s	remaining: 1.97s
2214:	learn: 1.0948888	total: 5.54s	remaining: 1.96s
2215:	learn: 1.0944957	total: 5.54s	remaining: 1.96s
2216:	learn: 1.0938919	total: 5.54s	remaining: 1.96s
2217:	learn: 1.0932018	total: 5.54s	remaining: 1.95s
2218:	learn: 1.0927269	total: 5.55s	remaining: 1.95s
2219:	learn: 1.0920081	total: 5.55s	remaining: 1.

2398:	learn: 0.9939965	total: 6.08s	remaining: 1.52s
2399:	learn: 0.9935744	total: 6.08s	remaining: 1.52s
2400:	learn: 0.9926976	total: 6.08s	remaining: 1.52s
2401:	learn: 0.9920118	total: 6.09s	remaining: 1.51s
2402:	learn: 0.9915933	total: 6.09s	remaining: 1.51s
2403:	learn: 0.9911892	total: 6.09s	remaining: 1.51s
2404:	learn: 0.9906154	total: 6.09s	remaining: 1.51s
2405:	learn: 0.9903447	total: 6.1s	remaining: 1.5s
2406:	learn: 0.9898888	total: 6.1s	remaining: 1.5s
2407:	learn: 0.9890512	total: 6.1s	remaining: 1.5s
2408:	learn: 0.9882577	total: 6.1s	remaining: 1.5s
2409:	learn: 0.9879200	total: 6.11s	remaining: 1.5s
2410:	learn: 0.9873392	total: 6.11s	remaining: 1.49s
2411:	learn: 0.9868903	total: 6.11s	remaining: 1.49s
2412:	learn: 0.9865535	total: 6.11s	remaining: 1.49s
2413:	learn: 0.9860796	total: 6.12s	remaining: 1.48s
2414:	learn: 0.9860296	total: 6.12s	remaining: 1.48s
2415:	learn: 0.9852460	total: 6.12s	remaining: 1.48s
2416:	learn: 0.9850112	total: 6.12s	remaining: 1.48s
24

2558:	learn: 0.9177379	total: 6.46s	remaining: 1.11s
2559:	learn: 0.9169546	total: 6.46s	remaining: 1.11s
2560:	learn: 0.9163930	total: 6.46s	remaining: 1.11s
2561:	learn: 0.9159471	total: 6.46s	remaining: 1.1s
2562:	learn: 0.9155774	total: 6.47s	remaining: 1.1s
2563:	learn: 0.9148785	total: 6.47s	remaining: 1.1s
2564:	learn: 0.9143202	total: 6.47s	remaining: 1.1s
2565:	learn: 0.9136302	total: 6.47s	remaining: 1.09s
2566:	learn: 0.9131660	total: 6.48s	remaining: 1.09s
2567:	learn: 0.9126878	total: 6.48s	remaining: 1.09s
2568:	learn: 0.9121897	total: 6.48s	remaining: 1.09s
2569:	learn: 0.9118161	total: 6.48s	remaining: 1.08s
2570:	learn: 0.9112437	total: 6.49s	remaining: 1.08s
2571:	learn: 0.9107609	total: 6.49s	remaining: 1.08s
2572:	learn: 0.9098639	total: 6.49s	remaining: 1.08s
2573:	learn: 0.9098220	total: 6.49s	remaining: 1.07s
2574:	learn: 0.9094964	total: 6.5s	remaining: 1.07s
2575:	learn: 0.9094609	total: 6.5s	remaining: 1.07s
2576:	learn: 0.9088951	total: 6.5s	remaining: 1.07s


2785:	learn: 0.8213392	total: 7.02s	remaining: 539ms
2786:	learn: 0.8210993	total: 7.03s	remaining: 537ms
2787:	learn: 0.8207783	total: 7.03s	remaining: 534ms
2788:	learn: 0.8204195	total: 7.03s	remaining: 532ms
2789:	learn: 0.8200912	total: 7.03s	remaining: 529ms
2790:	learn: 0.8193902	total: 7.04s	remaining: 527ms
2791:	learn: 0.8191987	total: 7.04s	remaining: 524ms
2792:	learn: 0.8187589	total: 7.04s	remaining: 522ms
2793:	learn: 0.8182560	total: 7.04s	remaining: 519ms
2794:	learn: 0.8178122	total: 7.04s	remaining: 517ms
2795:	learn: 0.8176355	total: 7.05s	remaining: 514ms
2796:	learn: 0.8172928	total: 7.05s	remaining: 512ms
2797:	learn: 0.8171048	total: 7.05s	remaining: 509ms
2798:	learn: 0.8166090	total: 7.05s	remaining: 507ms
2799:	learn: 0.8165780	total: 7.06s	remaining: 504ms
2800:	learn: 0.8162135	total: 7.06s	remaining: 502ms
2801:	learn: 0.8159747	total: 7.06s	remaining: 499ms
2802:	learn: 0.8155453	total: 7.07s	remaining: 497ms
2803:	learn: 0.8149915	total: 7.07s	remaining:

2945:	learn: 0.7593998	total: 7.4s	remaining: 136ms
2946:	learn: 0.7590305	total: 7.4s	remaining: 133ms
2947:	learn: 0.7586450	total: 7.4s	remaining: 131ms
2948:	learn: 0.7583343	total: 7.41s	remaining: 128ms
2949:	learn: 0.7579533	total: 7.41s	remaining: 126ms
2950:	learn: 0.7578349	total: 7.41s	remaining: 123ms
2951:	learn: 0.7575533	total: 7.41s	remaining: 121ms
2952:	learn: 0.7574566	total: 7.41s	remaining: 118ms
2953:	learn: 0.7570451	total: 7.42s	remaining: 116ms
2954:	learn: 0.7565838	total: 7.42s	remaining: 113ms
2955:	learn: 0.7561461	total: 7.42s	remaining: 110ms
2956:	learn: 0.7561201	total: 7.42s	remaining: 108ms
2957:	learn: 0.7556382	total: 7.43s	remaining: 105ms
2958:	learn: 0.7552997	total: 7.43s	remaining: 103ms
2959:	learn: 0.7549919	total: 7.43s	remaining: 100ms
2960:	learn: 0.7545780	total: 7.43s	remaining: 97.9ms
2961:	learn: 0.7544875	total: 7.44s	remaining: 95.4ms
2962:	learn: 0.7540119	total: 7.44s	remaining: 92.9ms
2963:	learn: 0.7536014	total: 7.44s	remaining:

In [28]:
stacked_models.fit(X, yt)
stacked_train_pred = stacked_models.predict(X)
stacked_pred = stacked_models.predict(test)
stacked_pred=inv_boxcox(stacked_pred, 0.3)
pred = pd.DataFrame(stacked_pred, columns=['SalePrice'])
ID = test_raw[['Id']]
sub1=pd.merge(ID, pred, left_on = ID.index, right_on = pred.index).drop(columns=['key_0'])
sub1.to_csv('../Submissions/pred_stacked_2.csv',index=False)
stacked_pred

Learning rate set to 0.017396
0:	learn: 14.7691469	total: 3.46ms	remaining: 10.4s
1:	learn: 14.5880851	total: 6.29ms	remaining: 9.43s
2:	learn: 14.4188203	total: 9.11ms	remaining: 9.1s
3:	learn: 14.2472070	total: 11.7ms	remaining: 8.76s
4:	learn: 14.0937298	total: 13.8ms	remaining: 8.28s
5:	learn: 13.9351549	total: 15.9ms	remaining: 7.93s
6:	learn: 13.7972010	total: 18.2ms	remaining: 7.78s
7:	learn: 13.6446048	total: 20.4ms	remaining: 7.62s
8:	learn: 13.5040481	total: 22.5ms	remaining: 7.49s
9:	learn: 13.3606378	total: 24.7ms	remaining: 7.4s
10:	learn: 13.2084976	total: 26.8ms	remaining: 7.29s
11:	learn: 13.0725660	total: 29.1ms	remaining: 7.26s
12:	learn: 12.9336183	total: 31.4ms	remaining: 7.21s
13:	learn: 12.7942577	total: 33.5ms	remaining: 7.15s
14:	learn: 12.6512209	total: 35.6ms	remaining: 7.09s
15:	learn: 12.5130767	total: 37.7ms	remaining: 7.03s
16:	learn: 12.3756976	total: 39.9ms	remaining: 7s
17:	learn: 12.2434636	total: 42.1ms	remaining: 6.97s
18:	learn: 12.1084139	total: 44

215:	learn: 4.5074114	total: 559ms	remaining: 7.21s
216:	learn: 4.4995043	total: 562ms	remaining: 7.21s
217:	learn: 4.4910936	total: 565ms	remaining: 7.21s
218:	learn: 4.4842987	total: 569ms	remaining: 7.22s
219:	learn: 4.4783396	total: 572ms	remaining: 7.22s
220:	learn: 4.4700061	total: 575ms	remaining: 7.22s
221:	learn: 4.4635039	total: 578ms	remaining: 7.23s
222:	learn: 4.4549630	total: 582ms	remaining: 7.24s
223:	learn: 4.4488052	total: 585ms	remaining: 7.25s
224:	learn: 4.4422827	total: 587ms	remaining: 7.25s
225:	learn: 4.4326944	total: 590ms	remaining: 7.24s
226:	learn: 4.4239948	total: 592ms	remaining: 7.23s
227:	learn: 4.4146166	total: 595ms	remaining: 7.23s
228:	learn: 4.4081603	total: 597ms	remaining: 7.23s
229:	learn: 4.4010651	total: 600ms	remaining: 7.22s
230:	learn: 4.3941452	total: 602ms	remaining: 7.22s
231:	learn: 4.3870141	total: 604ms	remaining: 7.21s
232:	learn: 4.3803886	total: 606ms	remaining: 7.2s
233:	learn: 4.3723548	total: 610ms	remaining: 7.21s
234:	learn: 4

380:	learn: 3.6966510	total: 934ms	remaining: 6.42s
381:	learn: 3.6946384	total: 937ms	remaining: 6.42s
382:	learn: 3.6903641	total: 940ms	remaining: 6.42s
383:	learn: 3.6872121	total: 943ms	remaining: 6.43s
384:	learn: 3.6840152	total: 947ms	remaining: 6.43s
385:	learn: 3.6825460	total: 950ms	remaining: 6.43s
386:	learn: 3.6806188	total: 953ms	remaining: 6.43s
387:	learn: 3.6776720	total: 955ms	remaining: 6.43s
388:	learn: 3.6758511	total: 957ms	remaining: 6.42s
389:	learn: 3.6728498	total: 959ms	remaining: 6.42s
390:	learn: 3.6707949	total: 962ms	remaining: 6.42s
391:	learn: 3.6667798	total: 964ms	remaining: 6.41s
392:	learn: 3.6628152	total: 967ms	remaining: 6.41s
393:	learn: 3.6608557	total: 970ms	remaining: 6.42s
394:	learn: 3.6579158	total: 973ms	remaining: 6.42s
395:	learn: 3.6550199	total: 975ms	remaining: 6.41s
396:	learn: 3.6524384	total: 978ms	remaining: 6.41s
397:	learn: 3.6503412	total: 980ms	remaining: 6.4s
398:	learn: 3.6467417	total: 982ms	remaining: 6.4s
399:	learn: 3.

592:	learn: 3.1422380	total: 1.5s	remaining: 6.09s
593:	learn: 3.1402888	total: 1.5s	remaining: 6.09s
594:	learn: 3.1381511	total: 1.5s	remaining: 6.09s
595:	learn: 3.1349215	total: 1.51s	remaining: 6.08s
596:	learn: 3.1337511	total: 1.51s	remaining: 6.08s
597:	learn: 3.1312513	total: 1.51s	remaining: 6.08s
598:	learn: 3.1293557	total: 1.52s	remaining: 6.08s
599:	learn: 3.1276667	total: 1.52s	remaining: 6.08s
600:	learn: 3.1246549	total: 1.52s	remaining: 6.08s
601:	learn: 3.1222078	total: 1.53s	remaining: 6.09s
602:	learn: 3.1193560	total: 1.53s	remaining: 6.09s
603:	learn: 3.1163864	total: 1.53s	remaining: 6.09s
604:	learn: 3.1132766	total: 1.54s	remaining: 6.08s
605:	learn: 3.1110932	total: 1.54s	remaining: 6.08s
606:	learn: 3.1087738	total: 1.54s	remaining: 6.08s
607:	learn: 3.1054000	total: 1.54s	remaining: 6.07s
608:	learn: 3.1021303	total: 1.55s	remaining: 6.07s
609:	learn: 3.1009760	total: 1.55s	remaining: 6.07s
610:	learn: 3.0983298	total: 1.55s	remaining: 6.07s
611:	learn: 3.0

752:	learn: 2.7941165	total: 1.88s	remaining: 5.59s
753:	learn: 2.7928043	total: 1.88s	remaining: 5.59s
754:	learn: 2.7916362	total: 1.88s	remaining: 5.59s
755:	learn: 2.7891688	total: 1.88s	remaining: 5.59s
756:	learn: 2.7872630	total: 1.88s	remaining: 5.58s
757:	learn: 2.7855300	total: 1.89s	remaining: 5.58s
758:	learn: 2.7833308	total: 1.89s	remaining: 5.58s
759:	learn: 2.7817238	total: 1.9s	remaining: 5.59s
760:	learn: 2.7798641	total: 1.9s	remaining: 5.58s
761:	learn: 2.7792064	total: 1.9s	remaining: 5.58s
762:	learn: 2.7780643	total: 1.9s	remaining: 5.58s
763:	learn: 2.7755876	total: 1.91s	remaining: 5.58s
764:	learn: 2.7739353	total: 1.91s	remaining: 5.58s
765:	learn: 2.7720408	total: 1.91s	remaining: 5.58s
766:	learn: 2.7699143	total: 1.91s	remaining: 5.57s
767:	learn: 2.7676319	total: 1.92s	remaining: 5.57s
768:	learn: 2.7664710	total: 1.92s	remaining: 5.57s
769:	learn: 2.7634658	total: 1.92s	remaining: 5.57s
770:	learn: 2.7610840	total: 1.92s	remaining: 5.56s
771:	learn: 2.75

...

2278:	learn: 1.1784170	total: 6.54s	remaining: 2.07s
2279:	learn: 1.1779126	total: 6.54s	remaining: 2.06s
2280:	learn: 1.1773135	total: 6.54s	remaining: 2.06s
2281:	learn: 1.1767436	total: 6.55s	remaining: 2.06s
2282:	learn: 1.1760784	total: 6.55s	remaining: 2.06s
2283:	learn: 1.1754543	total: 6.56s	remaining: 2.06s
2284:	learn: 1.1750731	total: 6.56s	remaining: 2.05s
2285:	learn: 1.1746733	total: 6.56s	remaining: 2.05s
2286:	learn: 1.1746120	total: 6.57s	remaining: 2.05s
2287:	learn: 1.1737233	total: 6.57s	remaining: 2.04s
2288:	learn: 1.1733322	total: 6.57s	remaining: 2.04s
2289:	learn: 1.1728876	total: 6.58s	remaining: 2.04s
2290:	learn: 1.1721997	total: 6.58s	remaining: 2.04s
2291:	learn: 1.1715706	total: 6.58s	remaining: 2.03s
2292:	learn: 1.1709597	total: 6.58s	remaining: 2.03s
2293:	learn: 1.1700655	total: 6.58s	remaining: 2.03s
2294:	learn: 1.1694567	total: 6.59s	remaining: 2.02s
2295:	learn: 1.1687392	total: 6.59s	remaining: 2.02s
2296:	learn: 1.1682509	total: 6.59s	remaining:

2479:	learn: 1.0760254	total: 7.1s	remaining: 1.49s
2480:	learn: 1.0755455	total: 7.11s	remaining: 1.49s
2481:	learn: 1.0747746	total: 7.11s	remaining: 1.48s
2482:	learn: 1.0743077	total: 7.11s	remaining: 1.48s
2483:	learn: 1.0734769	total: 7.12s	remaining: 1.48s
2484:	learn: 1.0730966	total: 7.12s	remaining: 1.48s
2485:	learn: 1.0726904	total: 7.12s	remaining: 1.47s
2486:	learn: 1.0717932	total: 7.13s	remaining: 1.47s
2487:	learn: 1.0713469	total: 7.13s	remaining: 1.47s
2488:	learn: 1.0708600	total: 7.13s	remaining: 1.46s
2489:	learn: 1.0703323	total: 7.13s	remaining: 1.46s
2490:	learn: 1.0697582	total: 7.14s	remaining: 1.46s
2491:	learn: 1.0693219	total: 7.14s	remaining: 1.46s
2492:	learn: 1.0687785	total: 7.14s	remaining: 1.45s
2493:	learn: 1.0681181	total: 7.14s	remaining: 1.45s
2494:	learn: 1.0676185	total: 7.15s	remaining: 1.45s
2495:	learn: 1.0670912	total: 7.15s	remaining: 1.44s
2496:	learn: 1.0662144	total: 7.15s	remaining: 1.44s
2497:	learn: 1.0655003	total: 7.16s	remaining: 

2688:	learn: 0.9836566	total: 7.67s	remaining: 887ms
2689:	learn: 0.9832431	total: 7.67s	remaining: 885ms
2690:	learn: 0.9829205	total: 7.68s	remaining: 882ms
2691:	learn: 0.9824602	total: 7.68s	remaining: 879ms
2692:	learn: 0.9824254	total: 7.69s	remaining: 877ms
2693:	learn: 0.9820150	total: 7.69s	remaining: 874ms
2694:	learn: 0.9818171	total: 7.7s	remaining: 871ms
2695:	learn: 0.9812095	total: 7.7s	remaining: 868ms
2696:	learn: 0.9806380	total: 7.7s	remaining: 865ms
2697:	learn: 0.9800716	total: 7.7s	remaining: 862ms
2698:	learn: 0.9799027	total: 7.71s	remaining: 860ms
2699:	learn: 0.9794125	total: 7.71s	remaining: 857ms
2700:	learn: 0.9788020	total: 7.71s	remaining: 854ms
2701:	learn: 0.9785232	total: 7.72s	remaining: 851ms
2702:	learn: 0.9782154	total: 7.72s	remaining: 848ms
2703:	learn: 0.9778826	total: 7.72s	remaining: 845ms
2704:	learn: 0.9772593	total: 7.72s	remaining: 843ms
2705:	learn: 0.9767931	total: 7.73s	remaining: 840ms
2706:	learn: 0.9767520	total: 7.73s	remaining: 837

2890:	learn: 0.9044247	total: 8.24s	remaining: 311ms
2891:	learn: 0.9039527	total: 8.25s	remaining: 308ms
2892:	learn: 0.9034640	total: 8.25s	remaining: 305ms
2893:	learn: 0.9029849	total: 8.25s	remaining: 302ms
2894:	learn: 0.9024297	total: 8.26s	remaining: 300ms
2895:	learn: 0.9019966	total: 8.26s	remaining: 297ms
2896:	learn: 0.9017266	total: 8.27s	remaining: 294ms
2897:	learn: 0.9009998	total: 8.27s	remaining: 291ms
2898:	learn: 0.9007372	total: 8.27s	remaining: 288ms
2899:	learn: 0.9007022	total: 8.27s	remaining: 285ms
2900:	learn: 0.9003219	total: 8.28s	remaining: 282ms
2901:	learn: 0.8999131	total: 8.28s	remaining: 280ms
2902:	learn: 0.8996803	total: 8.28s	remaining: 277ms
2903:	learn: 0.8993905	total: 8.28s	remaining: 274ms
2904:	learn: 0.8988321	total: 8.29s	remaining: 271ms
2905:	learn: 0.8985998	total: 8.29s	remaining: 268ms
2906:	learn: 0.8979717	total: 8.29s	remaining: 265ms
2907:	learn: 0.8976681	total: 8.29s	remaining: 262ms
2908:	learn: 0.8974358	total: 8.3s	remaining: 

array([124107.31663452, 158991.50762493, 189283.47607376, ...,
       169116.16339938, 124650.11429528, 211472.600603  ])

In [29]:
lightgbm=pd.read_csv('../Submissions/pred_lightgbm.csv')
stacked2=pd.read_csv('../Submissions/pred_stacked_2.csv')
prediction=0.7*stacked2.SalePrice+0.3*lightgbm.SalePrice
pred = pd.DataFrame(prediction, columns=['SalePrice'])
ID = test_raw[['Id']]
sub1=pd.merge(ID, pred, left_on = ID.index, right_on = pred.index).drop(columns=['key_0'])
sub1.to_csv('../Submissions/pred_final_prediction1.csv',index=False)